## Install the required libraries

In [1]:
#!pip install scikit-multilearn
#!pip install catboost

## Import the required libraries

In [59]:
# Import the required libraries
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
import re
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import MinMaxScaler
import itertools
import tqdm

## Load the Training and Test sets.

In [3]:
#load the Training and Test sets.
train = pd.read_csv('Train.csv')
test = pd.read_csv('Test.csv')
submission = pd.read_csv('SampleSubmission.csv')

## Join Train and Test
The training and the test sets are combined to make sure both sets are normalized using the same scale.

In [4]:
joined  = pd.concat([train,test])
joined

ID  join_date sex marital_status  birth_year branch_code  \
0     4WKQSBB   1/2/2019   F              M        1987        1X1H   
1     CP5S02H   1/6/2019   F              M        1981        UAOD   
2     2YKDILJ   1/6/2013   M              U        1991        748L   
3     2S9E81J   1/8/2019   M              M        1990        1X1H   
4     BHDYVFT   1/8/2019   M              M        1990        748L   
...       ...        ...  ..            ...         ...         ...   
9995  0GMU5UH   1/4/2019   F              M        1986        748L   
9996  I9W11CD   1/8/2019   M              M        1980        UAOD   
9997  42WTEGT   1/4/2018   M              M        1993        748L   
9998  8EKC4O9   1/5/2015   F              U        1981        49BM   
9999  WHII93K  1/11/2018   M              U        1977        94KC   

     occupation_code occupation_category_code  P5DA  RIBP  ...  AHXO  BSTQ  \
0               2A7I                     T4MS     0     0  ...     0     0   
1               2A7I                     T4MS     0     0  ...     0     0   
2               QZYX                     90QI     0     0  ...     0     0   
3               BP09                     56SI     0     0  ...     0     0   
4               NO3L                     T4MS     0     0  ...     0     0   
...              ...                      ...   ...   ...  ...   ...   ...   
9995            2A7I                     T4MS     0     0  ...     0     0   
9996            0KID                     T4MS     0     0  ...     0     0   
9997            SST3                     56SI     0     0  ...     0     0   
9998            2A7I                     T4MS     0     0  ...     0     0   
9999            2A7I                     T4MS     0     0  ...     0     0   

      FM3X  K6QO  QBOL  JWFN  JZ9D  J9JW  GHYX  ECY3  
0        0     1     0     0     0     0     0     0  
1        0     1     0     0     0     0     0     0  
2        0     0     0     0     0     0     0     1  
3        0     1     0     0     0     0     0     0  
4        0     0     0     0     1     1     0     0  
...    ...   ...   ...   ...   ...   ...   ...   ...  
9995     0     0     1     0     1     0     0     0  
9996     0     0     0     0     0     0     0     0  
9997     0     1     0     0     0     0     0     0  
9998     0     0     0     0     0     0     0     0  
9999     0     1     0     0     0     0     0     0  

[39132 rows x 29 columns]

### Check for null values
join_date has 3 null entries

In [5]:
joined.isnull().sum()

ID                          0
join_date                   3
sex                         0
marital_status              0
birth_year                  0
branch_code                 0
occupation_code             0
occupation_category_code    0
P5DA                        0
RIBP                        0
8NN1                        0
7POT                        0
66FJ                        0
GYSR                        0
SOP4                        0
RVSZ                        0
PYUQ                        0
LJR9                        0
N2MW                        0
AHXO                        0
BSTQ                        0
FM3X                        0
K6QO                        0
QBOL                        0
JWFN                        0
JZ9D                        0
J9JW                        0
GHYX                        0
ECY3                        0
dtype: int64

### Replace null values

In [6]:
joined["join_date"].fillna("1/1/2020", inplace = True)

### Split join_date to Day, Month and Year

In [7]:
joined[['Day','Month','Year']] = joined.join_date.str.split("/",expand=True,)

### Change data-type of Day, Year and Month to int

In [8]:
joined["Day"] = joined['Day'].astype(int)
joined["Year"] = joined.Year.astype(int)
joined["Month"] = joined.Month.astype(int)

### Calculate Age from join_date (Year) and birth_year

In [9]:
joined['Age'] = joined['Year'] - joined['birth_year']

### Use MinMax Scaler to normalize numerical columns

In [10]:
num_cols = ['Age','Year','Month','Day']
scaler = MinMaxScaler()
joined[num_cols] = scaler.fit_transform(joined[num_cols])

### Split the joined dataframe to the respective train and test sets

In [11]:
train  = joined.head(29132)
test = joined.tail(10000)

### Identify Product Features for the training and test sets.

In [12]:
features = train[['P5DA', 'RIBP', '8NN1',
       '7POT', '66FJ', 'GYSR', 'SOP4', 'RVSZ', 'PYUQ', 'LJR9', 'N2MW', 'AHXO','BSTQ', 'FM3X', 'K6QO', 'QBOL', 'JWFN', 'JZ9D', 'J9JW', 'GHYX', 'ECY3']]
features_test = test[['P5DA', 'RIBP', '8NN1',
       '7POT', '66FJ', 'GYSR', 'SOP4', 'RVSZ', 'PYUQ', 'LJR9', 'N2MW', 'AHXO',
       'BSTQ', 'FM3X', 'K6QO', 'QBOL', 'JWFN', 'JZ9D', 'J9JW', 'GHYX', 'ECY3']]


### Duplicate Input Products

The duplicates of all products are going to be used as extra features for the purpose of training the models. The original products serve as target variables.

In [13]:
# get the list of product columns
column_list = features.columns.tolist()

# append _input at the end of each product to distinguish it from the target variable
input_column_names = [name + '_input' for name in column_list]

In [14]:
# change the names of the original products to the one that has _input appended to it 
features.columns = input_column_names
features_test.columns = input_column_names

In [15]:
## include the original products to the training and test sets.
train = train.join(features)
test = test.join(features_test)

### Getting a binary number representation of all products

In [16]:
binaries = train[['P5DA', 'RIBP', '8NN1',
       '7POT', '66FJ', 'GYSR', 'SOP4', 'RVSZ', 'PYUQ', 'LJR9', 'N2MW', 'AHXO',
       'BSTQ', 'FM3X', 'K6QO', 'QBOL', 'JWFN', 'JZ9D', 'J9JW', 'GHYX', 'ECY3']].astype(str).agg(''.join, axis=1)
binaries

0        000000010000001000000
1        000000010000001000000
2        000000110000000000001
3        000000010000001000000
4        000000000000000001100
                 ...          
29127    000000010000001000000
29128    000000010000001000000
29129    000000010000001000000
29130    000000010000001000000
29131    000000010000001000000
Length: 29132, dtype: object

### Populate the data-frame by duplicating each row as many times as the number of ones in the list of products.

In [17]:

modified_binaries = []

for binary in binaries:
    i = 0
    j = 0
    current_binaries = []
    for digit in binary:
        modified_binary = ''
        
        
        if(digit=='1'):
                modified_binary = binary
                modified_string = modified_binary[:i] + '0' + modified_binary[i + 1:]
                #print(modified_string)
                current_binaries.append(modified_string)
                j+=1
        i+=1
    modified_binaries.append(current_binaries)

In [18]:
train['binaries'] = modified_binaries
train['binaries'] = train['binaries']
df = train.explode('binaries').fillna('')


### A function to separate each digit in the binary column with a comma

In [19]:
# a function that accepts a string and adds a comma b/n each character.
def separate_binaries(row):
        separated_binary = re.sub(r'([0-9])(?!$)', r'\1,', row)
        
        return separated_binary


In [20]:
df['binaries'] = df.apply(lambda row: separate_binaries(row['binaries']),axis=1)

In [21]:
df

ID join_date sex marital_status  birth_year branch_code  \
0      4WKQSBB  1/2/2019   F              M        1987        1X1H   
0      4WKQSBB  1/2/2019   F              M        1987        1X1H   
1      CP5S02H  1/6/2019   F              M        1981        UAOD   
1      CP5S02H  1/6/2019   F              M        1981        UAOD   
2      2YKDILJ  1/6/2013   M              U        1991        748L   
...        ...       ...  ..            ...         ...         ...   
29129  MVXG2LC  1/2/2019   M              M        1985        BOAS   
29130  BUQ8DQN  1/7/2019   M              M        1989        UAOD   
29130  BUQ8DQN  1/7/2019   M              M        1989        UAOD   
29131  DEJBWYU  1/3/2020   M              M        1975        94KC   
29131  DEJBWYU  1/3/2020   M              M        1975        94KC   

      occupation_code occupation_category_code  P5DA  RIBP  ...  BSTQ_input  \
0                2A7I                     T4MS     0     0  ...           0   
0                2A7I                     T4MS     0     0  ...           0   
1                2A7I                     T4MS     0     0  ...           0   
1                2A7I                     T4MS     0     0  ...           0   
2                QZYX                     90QI     0     0  ...           0   
...               ...                      ...   ...   ...  ...         ...   
29129            6PE7                     T4MS     0     0  ...           0   
29130            2A7I                     T4MS     0     0  ...           0   
29130            2A7I                     T4MS     0     0  ...           0   
29131            31JW                     90QI     0     0  ...           0   
29131            31JW                     90QI     0     0  ...           0   

       FM3X_input  K6QO_input  QBOL_input  JWFN_input  JZ9D_input  J9JW_input  \
0               0           1           0           0           0           0   
0               0           1           0           0           0           0   
1               0           1           0           0           0           0   
1               0           1           0           0           0           0   
2               0           0           0           0           0           0   
...           ...         ...         ...         ...         ...         ...   
29129           0           1           0           0           0           0   
29130           0           1           0           0           0           0   
29130           0           1           0           0           0           0   
29131           0           1           0           0           0           0   
29131           0           1           0           0           0           0   

       GHYX_input  ECY3_input                                   binaries  
0               0           0  0,0,0,0,0,0,0,0,0,0,0,0,0,0,1,0,0,0,0,0,0  
0               0           0  0,0,0,0,0,0,0,1,0,0,0,0,0,0,0,0,0,0,0,0,0  
1               0           0  0,0,0,0,0,0,0,0,0,0,0,0,0,0,1,0,0,0,0,0,0  
1               0           0  0,0,0,0,0,0,0,1,0,0,0,0,0,0,0,0,0,0,0,0,0  
2               0           1  0,0,0,0,0,0,0,1,0,0,0,0,0,0,0,0,0,0,0,0,1  
...           ...         ...                                        ...  
29129           0           0  0,0,0,0,0,0,0,1,0,0,0,0,0,0,0,0,0,0,0,0,0  
29130           0           0  0,0,0,0,0,0,0,0,0,0,0,0,0,0,1,0,0,0,0,0,0  
29130           0           0  0,0,0,0,0,0,0,1,0,0,0,0,0,0,0,0,0,0,0,0,0  
29131           0           0  0,0,0,0,0,0,0,0,0,0,0,0,0,0,1,0,0,0,0,0,0  
29131           0           0  0,0,0,0,0,0,0,1,0,0,0,0,0,0,0,0,0,0,0,0,0  

[66353 rows x 55 columns]

### Imitating the test data.
The test data has one of the products with a 1 entry changed to 0. That is one of the subscribed products is given as unsubscribed. The following cell changes one of the subscribed products to unsubscribed for each row of the dataframe. Remember we have duplicated each row as many times as the number of ones in the binary column of each row. So, we change a different product from 1 to 0 on each duplicate of the row.

In [22]:
df[['P5DA_input',
 'RIBP_input',
 '8NN1_input',
 '7POT_input',
 '66FJ_input',
 'GYSR_input',
 'SOP4_input',
 'RVSZ_input',
 'PYUQ_input',
 'LJR9_input',
 'N2MW_input',
 'AHXO_input',
 'BSTQ_input',
 'FM3X_input',
 'K6QO_input',
 'QBOL_input',
 'JWFN_input',
 'JZ9D_input',
 'J9JW_input',
 'GHYX_input',
 'ECY3_input',]] = df.binaries.str.split(',',expand=True,)

In [23]:
df

ID join_date sex marital_status  birth_year branch_code  \
0      4WKQSBB  1/2/2019   F              M        1987        1X1H   
0      4WKQSBB  1/2/2019   F              M        1987        1X1H   
1      CP5S02H  1/6/2019   F              M        1981        UAOD   
1      CP5S02H  1/6/2019   F              M        1981        UAOD   
2      2YKDILJ  1/6/2013   M              U        1991        748L   
...        ...       ...  ..            ...         ...         ...   
29129  MVXG2LC  1/2/2019   M              M        1985        BOAS   
29130  BUQ8DQN  1/7/2019   M              M        1989        UAOD   
29130  BUQ8DQN  1/7/2019   M              M        1989        UAOD   
29131  DEJBWYU  1/3/2020   M              M        1975        94KC   
29131  DEJBWYU  1/3/2020   M              M        1975        94KC   

      occupation_code occupation_category_code  P5DA  RIBP  ...  BSTQ_input  \
0                2A7I                     T4MS     0     0  ...           0   
0                2A7I                     T4MS     0     0  ...           0   
1                2A7I                     T4MS     0     0  ...           0   
1                2A7I                     T4MS     0     0  ...           0   
2                QZYX                     90QI     0     0  ...           0   
...               ...                      ...   ...   ...  ...         ...   
29129            6PE7                     T4MS     0     0  ...           0   
29130            2A7I                     T4MS     0     0  ...           0   
29130            2A7I                     T4MS     0     0  ...           0   
29131            31JW                     90QI     0     0  ...           0   
29131            31JW                     90QI     0     0  ...           0   

       FM3X_input  K6QO_input  QBOL_input  JWFN_input  JZ9D_input  J9JW_input  \
0               0           1           0           0           0           0   
0               0           0           0           0           0           0   
1               0           1           0           0           0           0   
1               0           0           0           0           0           0   
2               0           0           0           0           0           0   
...           ...         ...         ...         ...         ...         ...   
29129           0           0           0           0           0           0   
29130           0           1           0           0           0           0   
29130           0           0           0           0           0           0   
29131           0           1           0           0           0           0   
29131           0           0           0           0           0           0   

       GHYX_input  ECY3_input                                   binaries  
0               0           0  0,0,0,0,0,0,0,0,0,0,0,0,0,0,1,0,0,0,0,0,0  
0               0           0  0,0,0,0,0,0,0,1,0,0,0,0,0,0,0,0,0,0,0,0,0  
1               0           0  0,0,0,0,0,0,0,0,0,0,0,0,0,0,1,0,0,0,0,0,0  
1               0           0  0,0,0,0,0,0,0,1,0,0,0,0,0,0,0,0,0,0,0,0,0  
2               0           1  0,0,0,0,0,0,0,1,0,0,0,0,0,0,0,0,0,0,0,0,1  
...           ...         ...                                        ...  
29129           0           0  0,0,0,0,0,0,0,1,0,0,0,0,0,0,0,0,0,0,0,0,0  
29130           0           0  0,0,0,0,0,0,0,0,0,0,0,0,0,0,1,0,0,0,0,0,0  
29130           0           0  0,0,0,0,0,0,0,1,0,0,0,0,0,0,0,0,0,0,0,0,0  
29131           0           0  0,0,0,0,0,0,0,0,0,0,0,0,0,0,1,0,0,0,0,0,0  
29131           0           0  0,0,0,0,0,0,0,1,0,0,0,0,0,0,0,0,0,0,0,0,0  

[66353 rows x 55 columns]

### Drop unnecessary columns

In [24]:
# drop unnecessary columns
df = df.drop('ID', axis = 1)
df = df.drop('join_date', axis = 1)
df = df.drop('binaries', axis = 1)

In [25]:
test = test.drop('ID', axis = 1)
test = test.drop('join_date', axis = 1)

## Separate the training and test datasets to feature and target varaible

In [26]:
target = np.asarray(df[['P5DA', 'RIBP', '8NN1',
       '7POT', '66FJ', 'GYSR', 'SOP4', 'RVSZ', 'PYUQ', 'LJR9', 'N2MW', 'AHXO',
       'BSTQ', 'FM3X', 'K6QO', 'QBOL', 'JWFN', 'JZ9D', 'J9JW', 'GHYX', 'ECY3']], dtype=float)

target_test = np.asarray(test[['P5DA', 'RIBP', '8NN1',
       '7POT', '66FJ', 'GYSR', 'SOP4', 'RVSZ', 'PYUQ', 'LJR9', 'N2MW', 'AHXO',
       'BSTQ', 'FM3X', 'K6QO', 'QBOL', 'JWFN', 'JZ9D', 'J9JW', 'GHYX', 'ECY3']], dtype=float)
input_features = df.drop(['P5DA', 'RIBP', '8NN1',
       '7POT', '66FJ', 'GYSR', 'SOP4', 'RVSZ', 'PYUQ', 'LJR9', 'N2MW', 'AHXO',
       'BSTQ', 'FM3X', 'K6QO', 'QBOL', 'JWFN', 'JZ9D', 'J9JW', 'GHYX', 'ECY3'], axis=1, inplace=True)
input_features_test = test.drop(['P5DA', 'RIBP', '8NN1',
       '7POT', '66FJ', 'GYSR', 'SOP4', 'RVSZ', 'PYUQ', 'LJR9', 'N2MW', 'AHXO',
       'BSTQ', 'FM3X', 'K6QO', 'QBOL', 'JWFN', 'JZ9D', 'J9JW', 'GHYX', 'ECY3'], axis=1, inplace=True)

In [27]:
pd.set_option('display.max_columns', None)
test.head(2)

sex marital_status  birth_year branch_code occupation_code  \
0   M              M        1984        94KC            DZRV   
1   M              M        1996        1X1H            J9SY   

  occupation_category_code  Day     Month  Year       Age  P5DA_input  \
0                     90QI  0.0  1.000000   0.8  0.329114           0   
1                     90QI  0.0  0.818182   0.9  0.189873           0   

   RIBP_input  8NN1_input  7POT_input  66FJ_input  GYSR_input  SOP4_input  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   

   RVSZ_input  PYUQ_input  LJR9_input  N2MW_input  AHXO_input  BSTQ_input  \
0           1           0           0           0           0           0   
1           1           0           0           0           0           0   

   FM3X_input  K6QO_input  QBOL_input  JWFN_input  JZ9D_input  J9JW_input  \
0           0           0           0           0           0           0   
1           0           1           0           0           0           0   

   GHYX_input  ECY3_input  
0           0           0  
1           0           0

### One Hot Encoding of Categorical Variables

In [28]:
# apply one hot encoding on categorical variables
categorical_test = test[['sex','marital_status','branch_code','occupation_code','occupation_category_code']]
categorical_df = df[['sex','marital_status','branch_code','occupation_code','occupation_category_code']]
categorical_df = pd.get_dummies(categorical_df)
categorical_test = pd.get_dummies(categorical_test)

In [29]:
df = pd.concat([categorical_df, df], axis=1, join='inner')
df

sex_F  sex_M  marital_status_D  marital_status_M  marital_status_P  \
0          1      0                 0                 1                 0   
0          1      0                 0                 1                 0   
1          1      0                 0                 1                 0   
1          1      0                 0                 1                 0   
2          0      1                 0                 0                 0   
...      ...    ...               ...               ...               ...   
29129      0      1                 0                 1                 0   
29130      0      1                 0                 1                 0   
29130      0      1                 0                 1                 0   
29131      0      1                 0                 1                 0   
29131      0      1                 0                 1                 0   

       marital_status_R  marital_status_S  marital_status_U  marital_status_W  \
0                     0                 0                 0                 0   
0                     0                 0                 0                 0   
1                     0                 0                 0                 0   
1                     0                 0                 0                 0   
2                     0                 0                 1                 0   
...                 ...               ...               ...               ...   
29129                 0                 0                 0                 0   
29130                 0                 0                 0                 0   
29130                 0                 0                 0                 0   
29131                 0                 0                 0                 0   
29131                 0                 0                 0                 0   

       marital_status_f  branch_code_1X1H  branch_code_30H5  branch_code_49BM  \
0                     0                 1                 0                 0   
0                     0                 1                 0                 0   
1                     0                 0                 0                 0   
1                     0                 0                 0                 0   
2                     0                 0                 0                 0   
...                 ...               ...               ...               ...   
29129                 0                 0                 0                 0   
29130                 0                 0                 0                 0   
29130                 0                 0                 0                 0   
29131                 0                 0                 0                 0   
29131                 0                 0                 0                 0   

       branch_code_748L  branch_code_94KC  branch_code_9F9T  branch_code_BOAS  \
0                     0                 0                 0                 0   
0                     0                 0                 0                 0   
1                     0                 0                 0                 0   
1                     0                 0                 0                 0   
2                     1                 0                 0                 0   
...                 ...               ...               ...               ...   
29129                 0                 0                 0                 1   
29130                 0                 0                 0                 0   
29130                 0                 0                 0                 0   
29131                 0                 1                 0                 0   
29131                 0                 1                 0                 0   

       branch_code_E5SW  branch_code_EU3L  branch_code_O4JC  branch_code_O67J  \
0                     0                 0                 0                 0   
0

In [30]:
test = categorical_test.join(test)
test

sex_F  sex_M  marital_status_D  marital_status_F  marital_status_M  \
0         0      1                 0                 0                 1   
1         0      1                 0                 0                 1   
2         1      0                 0                 0                 0   
3         0      1                 0                 0                 1   
4         1      0                 0                 0                 1   
...     ...    ...               ...               ...               ...   
9995      1      0                 0                 0                 1   
9996      0      1                 0                 0                 1   
9997      0      1                 0                 0                 1   
9998      1      0                 0                 0                 0   
9999      0      1                 0                 0                 0   

      marital_status_P  marital_status_R  marital_status_S  marital_status_U  \
0                    0                 0                 0                 0   
1                    0                 0                 0                 0   
2                    0                 0                 0                 0   
3                    0                 0                 0                 0   
4                    0                 0                 0                 0   
...                ...               ...               ...               ...   
9995                 0                 0                 0                 0   
9996                 0                 0                 0                 0   
9997                 0                 0                 0                 0   
9998                 0                 0                 0                 1   
9999                 0                 0                 0                 1   

      marital_status_W  branch_code_1X1H  branch_code_30H5  branch_code_49BM  \
0                    0                 0                 0                 0   
1                    0                 1                 0                 0   
2                    1                 0                 0                 0   
3                    0                 0                 0                 0   
4                    0                 0                 0                 0   
...                ...               ...               ...               ...   
9995                 0                 0                 0                 0   
9996                 0                 0                 0                 0   
9997                 0                 0                 0                 0   
9998                 0                 0                 0                 1   
9999                 0                 0                 0                 0   

      branch_code_748L  branch_code_94KC  branch_code_9F9T  branch_code_BOAS  \
0                    0                 1                 0                 0   
1                    0                 0                 0                 0   
2                    0                 0                 0                 0   
3                    0                 1                 0                 0   
4                    0                 0                 0                 0   
...                ...               ...               ...               ...   
9995                 1                 0                 0                 0   
9996                 0                 0                 0                 0   
9997                 1                 0                 0                 0   
9998                 0                 0                 0                 0   
9999                 0                 1                 0                 0   

      branch_code_E5SW  branch_code_EU3L  branch_code_O4JC  branch_code_O67J  \
0                    0                 0                 0                 0   
1                    0                 0          

## Make sure the number of columns of training and test variables is the same

In [31]:
missing_cols = set( df.columns ) - set( test.columns )
# Add a missing column in test set with default value equal to 0
for c in missing_cols:
    test[c] = 0
# Ensure the order of column in the test set is in the same order than in train set
test = test[df.columns]

In [32]:
test

sex_F  sex_M  marital_status_D  marital_status_M  marital_status_P  \
0         0      1                 0                 1                 0   
1         0      1                 0                 1                 0   
2         1      0                 0                 0                 0   
3         0      1                 0                 1                 0   
4         1      0                 0                 1                 0   
...     ...    ...               ...               ...               ...   
9995      1      0                 0                 1                 0   
9996      0      1                 0                 1                 0   
9997      0      1                 0                 1                 0   
9998      1      0                 0                 0                 0   
9999      0      1                 0                 0                 0   

      marital_status_R  marital_status_S  marital_status_U  marital_status_W  \
0                    0                 0                 0                 0   
1                    0                 0                 0                 0   
2                    0                 0                 0                 1   
3                    0                 0                 0                 0   
4                    0                 0                 0                 0   
...                ...               ...               ...               ...   
9995                 0                 0                 0                 0   
9996                 0                 0                 0                 0   
9997                 0                 0                 0                 0   
9998                 0                 0                 1                 0   
9999                 0                 0                 1                 0   

      marital_status_f  branch_code_1X1H  branch_code_30H5  branch_code_49BM  \
0                    0                 0                 0                 0   
1                    0                 1                 0                 0   
2                    0                 0                 0                 0   
3                    0                 0                 0                 0   
4                    0                 0                 0                 0   
...                ...               ...               ...               ...   
9995                 0                 0                 0                 0   
9996                 0                 0                 0                 0   
9997                 0                 0                 0                 0   
9998                 0                 0                 0                 1   
9999                 0                 0                 0                 0   

      branch_code_748L  branch_code_94KC  branch_code_9F9T  branch_code_BOAS  \
0                    0                 1                 0                 0   
1                    0                 0                 0                 0   
2                    0                 0                 0                 0   
3                    0                 1                 0                 0   
4                    0                 0                 0                 0   
...                ...               ...               ...               ...   
9995                 1                 0                 0                 0   
9996                 0                 0                 0                 0   
9997                 1                 0                 0                 0   
9998                 0                 0                 0                 0   
9999                 0                 1                 0                 0   

      branch_code_E5SW  branch_code_EU3L  branch_code_O4JC  branch_code_O67J  \
0                    0                 0                 0                 0   
1                    0                 0          

## Drop Original Categorical columns
We are dropping the original categorical columns because they are already represented by one-hot encoding

In [33]:
df = df.drop(['sex','marital_status','branch_code','occupation_code','occupation_category_code','birth_year','Day','Month'] ,axis=1)
test = test.drop(['sex','marital_status','branch_code','occupation_code','occupation_category_code','birth_year','Day','Month'],axis=1)

In [34]:
test

sex_F  sex_M  marital_status_D  marital_status_M  marital_status_P  \
0         0      1                 0                 1                 0   
1         0      1                 0                 1                 0   
2         1      0                 0                 0                 0   
3         0      1                 0                 1                 0   
4         1      0                 0                 1                 0   
...     ...    ...               ...               ...               ...   
9995      1      0                 0                 1                 0   
9996      0      1                 0                 1                 0   
9997      0      1                 0                 1                 0   
9998      1      0                 0                 0                 0   
9999      0      1                 0                 0                 0   

      marital_status_R  marital_status_S  marital_status_U  marital_status_W  \
0                    0                 0                 0                 0   
1                    0                 0                 0                 0   
2                    0                 0                 0                 1   
3                    0                 0                 0                 0   
4                    0                 0                 0                 0   
...                ...               ...               ...               ...   
9995                 0                 0                 0                 0   
9996                 0                 0                 0                 0   
9997                 0                 0                 0                 0   
9998                 0                 0                 1                 0   
9999                 0                 0                 1                 0   

      marital_status_f  branch_code_1X1H  branch_code_30H5  branch_code_49BM  \
0                    0                 0                 0                 0   
1                    0                 1                 0                 0   
2                    0                 0                 0                 0   
3                    0                 0                 0                 0   
4                    0                 0                 0                 0   
...                ...               ...               ...               ...   
9995                 0                 0                 0                 0   
9996                 0                 0                 0                 0   
9997                 0                 0                 0                 0   
9998                 0                 0                 0                 1   
9999                 0                 0                 0                 0   

      branch_code_748L  branch_code_94KC  branch_code_9F9T  branch_code_BOAS  \
0                    0                 1                 0                 0   
1                    0                 0                 0                 0   
2                    0                 0                 0                 0   
3                    0                 1                 0                 0   
4                    0                 0                 0                 0   
...                ...               ...               ...               ...   
9995                 1                 0                 0                 0   
9996                 0                 0                 0                 0   
9997                 1                 0                 0                 0   
9998                 0                 0                 0                 0   
9999                 0                 1                 0                 0   

      branch_code_E5SW  branch_code_EU3L  branch_code_O4JC  branch_code_O67J  \
0                    0                 0                 0                 0   
1                    0                 0          

In [35]:
df

sex_F  sex_M  marital_status_D  marital_status_M  marital_status_P  \
0          1      0                 0                 1                 0   
0          1      0                 0                 1                 0   
1          1      0                 0                 1                 0   
1          1      0                 0                 1                 0   
2          0      1                 0                 0                 0   
...      ...    ...               ...               ...               ...   
29129      0      1                 0                 1                 0   
29130      0      1                 0                 1                 0   
29130      0      1                 0                 1                 0   
29131      0      1                 0                 1                 0   
29131      0      1                 0                 1                 0   

       marital_status_R  marital_status_S  marital_status_U  marital_status_W  \
0                     0                 0                 0                 0   
0                     0                 0                 0                 0   
1                     0                 0                 0                 0   
1                     0                 0                 0                 0   
2                     0                 0                 1                 0   
...                 ...               ...               ...               ...   
29129                 0                 0                 0                 0   
29130                 0                 0                 0                 0   
29130                 0                 0                 0                 0   
29131                 0                 0                 0                 0   
29131                 0                 0                 0                 0   

       marital_status_f  branch_code_1X1H  branch_code_30H5  branch_code_49BM  \
0                     0                 1                 0                 0   
0                     0                 1                 0                 0   
1                     0                 0                 0                 0   
1                     0                 0                 0                 0   
2                     0                 0                 0                 0   
...                 ...               ...               ...               ...   
29129                 0                 0                 0                 0   
29130                 0                 0                 0                 0   
29130                 0                 0                 0                 0   
29131                 0                 0                 0                 0   
29131                 0                 0                 0                 0   

       branch_code_748L  branch_code_94KC  branch_code_9F9T  branch_code_BOAS  \
0                     0                 0                 0                 0   
0                     0                 0                 0                 0   
1                     0                 0                 0                 0   
1                     0                 0                 0                 0   
2                     1                 0                 0                 0   
...                 ...               ...               ...               ...   
29129                 0                 0                 0                 1   
29130                 0                 0                 0                 0   
29130                 0                 0                 0                 0   
29131                 0                 1                 0                 0   
29131                 0                 1                 0                 0   

       branch_code_E5SW  branch_code_EU3L  branch_code_O4JC  branch_code_O67J  \
0                     0                 0                 0                 0   
0

### Split the trianing set to training and validation sets

In [36]:
X_train, X_test, y_train, y_test = train_test_split(df, target, test_size=0.1) 

### Change the data-type of encoded entries to float

In [37]:
X_train = X_train.astype(float)
X_test = X_test.astype(float)
test = test.astype(float)

### Import libraries related to Model training and evaluation

In [38]:
from skmultilearn.problem_transform import ClassifierChain, LabelPowerset
from sklearn.model_selection import GridSearchCV
from sklearn.naive_bayes import GaussianNB
from sklearn.ensemble import RandomForestClassifier
from skmultilearn.cluster import NetworkXLabelGraphClusterer
from skmultilearn.cluster import LabelCooccurrenceGraphBuilder
from skmultilearn.ensemble import LabelSpacePartitioningClassifier
from skmultilearn.ensemble import MajorityVotingClassifier
from skmultilearn.cluster import FixedLabelSpaceClusterer
from skmultilearn.problem_transform import ClassifierChain
from sklearn.naive_bayes import GaussianNB
from sklearn.preprocessing import MultiLabelBinarizer
from skmultilearn.problem_transform import BinaryRelevance
from sklearn.ensemble import RandomForestClassifier
from skmultilearn.problem_transform import LabelPowerset
from xgboost import XGBClassifier
from skmultilearn.adapt import MLkNN
from sklearn.model_selection import GridSearchCV
from catboost import CatBoostClassifier
from sklearn.neural_network import MLPClassifier
from lightgbm import LGBMModel,LGBMClassifier
from sklearn.metrics import log_loss, accuracy_score 




## Stacking LGBM & Catboost Classifiers

In [99]:
models = []
models.append(CatBoostClassifier(random_state=17, depth = 5,learning_rate=0.05))
models.append(CatBoostClassifier(random_state=90, num_trees=700, depth=5,learning_rate=0.05))
models.append(CatBoostClassifier(random_state=50, num_trees=500, depth = 5,learning_rate=0.05))
models.append(CatBoostClassifier(random_state=20, num_trees=1200, depth=5,learning_rate=0.05))
models.append(LGBMClassifier(n_estimators=150, silent=False, random_state =94,
                         max_depth=5,num_leaves=31,objective='binary'))
models.append(CatBoostClassifier(random_state=45))

In [100]:
classifiers = []

## Fit the classifiers

In [101]:
for model in models:
    classifier = ClassifierChain(
        classifier = model,
        require_dense = [False, True]
    )

    classifier.fit(X_train,y_train)
    classifiers.append(classifier)

0:	learn: 0.5372752	total: 23.6ms	remaining: 23.6s
1:	learn: 0.4072527	total: 44ms	remaining: 22s
2:	learn: 0.3207572	total: 60.3ms	remaining: 20s
3:	learn: 0.2526289	total: 78ms	remaining: 19.4s
4:	learn: 0.2010454	total: 92ms	remaining: 18.3s
5:	learn: 0.1496519	total: 106ms	remaining: 17.6s
6:	learn: 0.1155434	total: 120ms	remaining: 17s
7:	learn: 0.0895390	total: 134ms	remaining: 16.6s
8:	learn: 0.0666318	total: 148ms	remaining: 16.3s
9:	learn: 0.0505246	total: 161ms	remaining: 16s
10:	learn: 0.0389052	total: 175ms	remaining: 15.7s
11:	learn: 0.0306435	total: 192ms	remaining: 15.8s
12:	learn: 0.0241297	total: 207ms	remaining: 15.7s
13:	learn: 0.0194027	total: 225ms	remaining: 15.9s
14:	learn: 0.0166690	total: 245ms	remaining: 16.1s
15:	learn: 0.0136517	total: 260ms	remaining: 16s
16:	learn: 0.0113750	total: 274ms	remaining: 15.9s
17:	learn: 0.0096130	total: 290ms	remaining: 15.8s
18:	learn: 0.0082496	total: 304ms	remaining: 15.7s
19:	learn: 0.0075211	total: 318ms	remaining: 15.6s
2

167:	learn: 0.0017310	total: 2.61s	remaining: 12.9s
168:	learn: 0.0017276	total: 2.63s	remaining: 12.9s
169:	learn: 0.0017223	total: 2.64s	remaining: 12.9s
170:	learn: 0.0017176	total: 2.66s	remaining: 12.9s
171:	learn: 0.0017173	total: 2.67s	remaining: 12.9s
172:	learn: 0.0017110	total: 2.68s	remaining: 12.8s
173:	learn: 0.0017108	total: 2.7s	remaining: 12.8s
174:	learn: 0.0017105	total: 2.71s	remaining: 12.8s
175:	learn: 0.0017097	total: 2.73s	remaining: 12.8s
176:	learn: 0.0017080	total: 2.74s	remaining: 12.7s
177:	learn: 0.0017064	total: 2.75s	remaining: 12.7s
178:	learn: 0.0017052	total: 2.77s	remaining: 12.7s
179:	learn: 0.0017001	total: 2.78s	remaining: 12.7s
180:	learn: 0.0016948	total: 2.8s	remaining: 12.7s
181:	learn: 0.0016908	total: 2.81s	remaining: 12.6s
182:	learn: 0.0016820	total: 2.83s	remaining: 12.6s
183:	learn: 0.0016771	total: 2.84s	remaining: 12.6s
184:	learn: 0.0016719	total: 2.85s	remaining: 12.6s
185:	learn: 0.0016703	total: 2.87s	remaining: 12.6s
186:	learn: 0.

331:	learn: 0.0012256	total: 5.25s	remaining: 10.6s
332:	learn: 0.0012235	total: 5.27s	remaining: 10.5s
333:	learn: 0.0012215	total: 5.29s	remaining: 10.5s
334:	learn: 0.0012203	total: 5.31s	remaining: 10.5s
335:	learn: 0.0012194	total: 5.33s	remaining: 10.5s
336:	learn: 0.0012186	total: 5.35s	remaining: 10.5s
337:	learn: 0.0012154	total: 5.37s	remaining: 10.5s
338:	learn: 0.0012146	total: 5.39s	remaining: 10.5s
339:	learn: 0.0012138	total: 5.42s	remaining: 10.5s
340:	learn: 0.0012131	total: 5.43s	remaining: 10.5s
341:	learn: 0.0012111	total: 5.45s	remaining: 10.5s
342:	learn: 0.0012092	total: 5.47s	remaining: 10.5s
343:	learn: 0.0012063	total: 5.49s	remaining: 10.5s
344:	learn: 0.0012042	total: 5.52s	remaining: 10.5s
345:	learn: 0.0011968	total: 5.54s	remaining: 10.5s
346:	learn: 0.0011933	total: 5.56s	remaining: 10.5s
347:	learn: 0.0011918	total: 5.58s	remaining: 10.5s
348:	learn: 0.0011900	total: 5.6s	remaining: 10.5s
349:	learn: 0.0011893	total: 5.63s	remaining: 10.5s
350:	learn: 0

497:	learn: 0.0009114	total: 7.8s	remaining: 7.86s
498:	learn: 0.0009078	total: 7.82s	remaining: 7.85s
499:	learn: 0.0009059	total: 7.83s	remaining: 7.83s
500:	learn: 0.0009056	total: 7.85s	remaining: 7.82s
501:	learn: 0.0009051	total: 7.86s	remaining: 7.8s
502:	learn: 0.0009045	total: 7.88s	remaining: 7.78s
503:	learn: 0.0009010	total: 7.89s	remaining: 7.76s
504:	learn: 0.0008969	total: 7.9s	remaining: 7.75s
505:	learn: 0.0008935	total: 7.92s	remaining: 7.73s
506:	learn: 0.0008935	total: 7.93s	remaining: 7.71s
507:	learn: 0.0008897	total: 7.94s	remaining: 7.69s
508:	learn: 0.0008894	total: 7.96s	remaining: 7.68s
509:	learn: 0.0008889	total: 7.97s	remaining: 7.66s
510:	learn: 0.0008854	total: 7.99s	remaining: 7.65s
511:	learn: 0.0008853	total: 8s	remaining: 7.63s
512:	learn: 0.0008822	total: 8.02s	remaining: 7.61s
513:	learn: 0.0008822	total: 8.03s	remaining: 7.59s
514:	learn: 0.0008821	total: 8.04s	remaining: 7.58s
515:	learn: 0.0008821	total: 8.06s	remaining: 7.56s
516:	learn: 0.0008

656:	learn: 0.0007251	total: 10.6s	remaining: 5.52s
657:	learn: 0.0007220	total: 10.6s	remaining: 5.5s
658:	learn: 0.0007216	total: 10.6s	remaining: 5.49s
659:	learn: 0.0007215	total: 10.6s	remaining: 5.47s
660:	learn: 0.0007212	total: 10.6s	remaining: 5.46s
661:	learn: 0.0007199	total: 10.7s	remaining: 5.44s
662:	learn: 0.0007192	total: 10.7s	remaining: 5.43s
663:	learn: 0.0007168	total: 10.7s	remaining: 5.42s
664:	learn: 0.0007145	total: 10.7s	remaining: 5.4s
665:	learn: 0.0007132	total: 10.8s	remaining: 5.39s
666:	learn: 0.0007130	total: 10.8s	remaining: 5.38s
667:	learn: 0.0007127	total: 10.8s	remaining: 5.37s
668:	learn: 0.0007121	total: 10.8s	remaining: 5.36s
669:	learn: 0.0007101	total: 10.8s	remaining: 5.34s
670:	learn: 0.0007095	total: 10.9s	remaining: 5.33s
671:	learn: 0.0007094	total: 10.9s	remaining: 5.31s
672:	learn: 0.0007064	total: 10.9s	remaining: 5.3s
673:	learn: 0.0007063	total: 10.9s	remaining: 5.29s
674:	learn: 0.0007060	total: 11s	remaining: 5.28s
675:	learn: 0.000

...

235:	learn: 0.0114782	total: 6.51s	remaining: 21.1s
236:	learn: 0.0113855	total: 6.54s	remaining: 21s
237:	learn: 0.0113438	total: 6.56s	remaining: 21s
238:	learn: 0.0112836	total: 6.59s	remaining: 21s
239:	learn: 0.0112407	total: 6.62s	remaining: 21s
240:	learn: 0.0111923	total: 6.66s	remaining: 21s
241:	learn: 0.0111156	total: 6.68s	remaining: 20.9s
242:	learn: 0.0109891	total: 6.71s	remaining: 20.9s
243:	learn: 0.0109443	total: 6.75s	remaining: 20.9s
244:	learn: 0.0109063	total: 6.78s	remaining: 20.9s
245:	learn: 0.0108924	total: 6.8s	remaining: 20.9s
246:	learn: 0.0108680	total: 6.83s	remaining: 20.8s
247:	learn: 0.0107843	total: 6.86s	remaining: 20.8s
248:	learn: 0.0107465	total: 6.9s	remaining: 20.8s
249:	learn: 0.0106924	total: 6.92s	remaining: 20.8s
250:	learn: 0.0106637	total: 6.95s	remaining: 20.8s
251:	learn: 0.0105813	total: 6.98s	remaining: 20.7s
252:	learn: 0.0104837	total: 7s	remaining: 20.7s
253:	learn: 0.0103576	total: 7.04s	remaining: 20.7s
254:	learn: 0.0103300	total

395:	learn: 0.0051249	total: 11.1s	remaining: 17s
396:	learn: 0.0050126	total: 11.2s	remaining: 17s
397:	learn: 0.0049865	total: 11.2s	remaining: 16.9s
398:	learn: 0.0049736	total: 11.2s	remaining: 16.9s
399:	learn: 0.0049603	total: 11.3s	remaining: 16.9s
400:	learn: 0.0049422	total: 11.3s	remaining: 16.9s
401:	learn: 0.0049314	total: 11.3s	remaining: 16.8s
402:	learn: 0.0049223	total: 11.3s	remaining: 16.8s
403:	learn: 0.0049080	total: 11.4s	remaining: 16.8s
404:	learn: 0.0048711	total: 11.4s	remaining: 16.8s
405:	learn: 0.0048648	total: 11.5s	remaining: 16.8s
406:	learn: 0.0048571	total: 11.5s	remaining: 16.8s
407:	learn: 0.0048433	total: 11.6s	remaining: 16.8s
408:	learn: 0.0047921	total: 11.6s	remaining: 16.7s
409:	learn: 0.0047830	total: 11.6s	remaining: 16.7s
410:	learn: 0.0047736	total: 11.7s	remaining: 16.7s
411:	learn: 0.0047205	total: 11.7s	remaining: 16.7s
412:	learn: 0.0047150	total: 11.7s	remaining: 16.6s
413:	learn: 0.0047136	total: 11.7s	remaining: 16.6s
414:	learn: 0.00

556:	learn: 0.0027867	total: 15.6s	remaining: 12.4s
557:	learn: 0.0027853	total: 15.6s	remaining: 12.4s
558:	learn: 0.0027817	total: 15.6s	remaining: 12.3s
559:	learn: 0.0027772	total: 15.6s	remaining: 12.3s
560:	learn: 0.0027763	total: 15.7s	remaining: 12.3s
561:	learn: 0.0027658	total: 15.7s	remaining: 12.2s
562:	learn: 0.0027564	total: 15.7s	remaining: 12.2s
563:	learn: 0.0027520	total: 15.7s	remaining: 12.2s
564:	learn: 0.0027457	total: 15.8s	remaining: 12.1s
565:	learn: 0.0027421	total: 15.8s	remaining: 12.1s
566:	learn: 0.0027361	total: 15.8s	remaining: 12.1s
567:	learn: 0.0027313	total: 15.8s	remaining: 12s
568:	learn: 0.0027283	total: 15.8s	remaining: 12s
569:	learn: 0.0027249	total: 15.9s	remaining: 12s
570:	learn: 0.0027208	total: 15.9s	remaining: 11.9s
571:	learn: 0.0027160	total: 15.9s	remaining: 11.9s
572:	learn: 0.0027076	total: 15.9s	remaining: 11.9s
573:	learn: 0.0027023	total: 16s	remaining: 11.8s
574:	learn: 0.0026925	total: 16s	remaining: 11.8s
575:	learn: 0.0026838	

722:	learn: 0.0017543	total: 19.3s	remaining: 7.41s
723:	learn: 0.0017513	total: 19.4s	remaining: 7.38s
724:	learn: 0.0017489	total: 19.4s	remaining: 7.35s
725:	learn: 0.0017471	total: 19.4s	remaining: 7.33s
726:	learn: 0.0017458	total: 19.4s	remaining: 7.3s
727:	learn: 0.0017433	total: 19.5s	remaining: 7.27s
728:	learn: 0.0017354	total: 19.5s	remaining: 7.25s
729:	learn: 0.0017354	total: 19.5s	remaining: 7.21s
730:	learn: 0.0017340	total: 19.5s	remaining: 7.19s
731:	learn: 0.0017293	total: 19.5s	remaining: 7.16s
732:	learn: 0.0017277	total: 19.6s	remaining: 7.13s
733:	learn: 0.0017277	total: 19.6s	remaining: 7.1s
734:	learn: 0.0017249	total: 19.6s	remaining: 7.07s
735:	learn: 0.0017051	total: 19.6s	remaining: 7.04s
736:	learn: 0.0016997	total: 19.7s	remaining: 7.01s
737:	learn: 0.0016984	total: 19.7s	remaining: 6.99s
738:	learn: 0.0016940	total: 19.7s	remaining: 6.96s
739:	learn: 0.0016918	total: 19.7s	remaining: 6.93s
740:	learn: 0.0016891	total: 19.8s	remaining: 6.9s
741:	learn: 0.0

881:	learn: 0.0011999	total: 22.9s	remaining: 3.06s
882:	learn: 0.0011969	total: 22.9s	remaining: 3.04s
883:	learn: 0.0011968	total: 22.9s	remaining: 3.01s
884:	learn: 0.0011961	total: 23s	remaining: 2.98s
885:	learn: 0.0011941	total: 23s	remaining: 2.96s
886:	learn: 0.0011924	total: 23s	remaining: 2.93s
887:	learn: 0.0011908	total: 23s	remaining: 2.9s
888:	learn: 0.0011890	total: 23.1s	remaining: 2.88s
889:	learn: 0.0011890	total: 23.1s	remaining: 2.85s
890:	learn: 0.0011873	total: 23.1s	remaining: 2.82s
891:	learn: 0.0011859	total: 23.1s	remaining: 2.8s
892:	learn: 0.0011857	total: 23.1s	remaining: 2.77s
893:	learn: 0.0011845	total: 23.1s	remaining: 2.74s
894:	learn: 0.0011845	total: 23.2s	remaining: 2.72s
895:	learn: 0.0011845	total: 23.2s	remaining: 2.69s
896:	learn: 0.0011842	total: 23.2s	remaining: 2.66s
897:	learn: 0.0011842	total: 23.2s	remaining: 2.64s
898:	learn: 0.0011834	total: 23.2s	remaining: 2.61s
899:	learn: 0.0011820	total: 23.3s	remaining: 2.58s
900:	learn: 0.0011808	

### Use the models to predict for the test set

In [102]:
predictions_list=[]
for i in range(len(classifiers)):
    predictions_list.append(classifiers[i].predict(test))

In [103]:
print(predictions.toarray()[0]) 

[0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0.]


### Get the probabilities for each product per customer

In [112]:
probabilities_list=[]
for i in range(len(classifiers)):
    probabilities_list.append(classifiers[i].predict_proba(test).todense())

#### Look at the probabilities of subscribing for the 21 products respectively for few customer.

In [105]:
print(probabilities_list)

[matrix([[5.21897400e-06, 1.30760790e-03, 2.34750148e-05, ...,
         1.26402802e-06, 1.01668456e-03, 4.36200894e-04],
        [2.23273761e-06, 8.55282419e-04, 3.19594929e-05, ...,
         1.29000610e-06, 2.49307660e-03, 1.20349726e-03],
        [7.94734133e-05, 2.74383239e-03, 8.97833330e-05, ...,
         1.63056835e-05, 2.12626798e-04, 1.52948855e-03],
        ...,
        [1.04225817e-06, 1.58627097e-04, 1.18714135e-05, ...,
         1.51235964e-06, 1.09671309e-05, 3.09694004e-05],
        [4.83679520e-04, 1.31928257e-01, 6.16724731e-03, ...,
         2.01174432e-05, 1.19243541e-03, 2.10491710e-03],
        [2.41250393e-06, 6.59365225e-03, 1.82883978e-03, ...,
         2.56316766e-06, 6.61922452e-06, 2.17242940e-05]]), matrix([[1.20863677e-05, 1.14866849e-03, 5.06416673e-05, ...,
         1.35209662e-06, 8.04432172e-04, 6.50238631e-04],
        [7.88368092e-06, 6.47571844e-04, 5.28385044e-05, ...,
         1.61994220e-06, 3.99942074e-03, 2.04825771e-03],
        [4.84436141e-05,

### Take the mean of all probabilities predicted by the models. 

In [113]:
probabilities = np.mean(probabilities_list, axis=0)

In [107]:
probabilities[0]

array([5.74181505e-06, 1.31718155e-03, 2.71495716e-05, 2.92137087e-04,
       2.07083609e-04, 4.29577477e-07, 7.97928952e-04, 9.99985798e-01,
       2.46633137e-03, 3.16578680e-04, 5.91694394e-04, 1.29525790e-04,
       1.85119436e-05, 8.97680702e-06, 9.76200086e-01, 8.92450683e-04,
       1.52879168e-04, 1.32213572e-05, 1.14615207e-06, 7.73669231e-04,
       6.73765771e-04])

### Arrange the probabilities as per the provided submission format

In [114]:
probabilities_1d = (itertools.chain.from_iterable(probabilities.tolist()))

In [115]:
submission['Label'] = list(probabilities_1d)

In [116]:
submission

ID X PCODE     Label
0       F86J5PC X P5DA  0.000006
1       F86J5PC X RIBP  0.001317
2       F86J5PC X 8NN1  0.000027
3       F86J5PC X 7POT  0.000292
4       F86J5PC X 66FJ  0.000207
...                ...       ...
209995  WHII93K X JWFN  0.000007
209996  WHII93K X JZ9D  0.000003
209997  WHII93K X J9JW  0.000002
209998  WHII93K X GHYX  0.000032
209999  WHII93K X ECY3  0.000071

[210000 rows x 2 columns]

### Write the submission dataframe to csv

In [117]:
submission.to_csv('submission_finale.csv', index=False)